In [1]:
import pandas as pd
import gradio as gr
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt
import seaborn as sns

/Users/cyberosa/.pyenv/versions/hf_dashboards/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
div_data = pd.read_parquet("../data/closed_markets_div.parquet")

In [8]:
div_data.loc[div_data["off_by_perc"]<=10]

currentAnswer                                          id  \
120           yes  0x5feab3ad41a2575461b06c5e911d67d3616ee17e   
148           yes  0x99a7e8be86a78cf2096a15887e9add122ff113d2   
194            no  0x34acf849dd645b559ddbf09059df39a1d9b10f18   

    openingTimestamp market_creator    opening_datetime  first_outcome_prob  \
120       1723420800     quickstart 2024-08-12 02:00:00              0.9034   
148       1723593600     quickstart 2024-08-14 02:00:00              0.9050   
194       1723939200     quickstart 2024-08-18 02:00:00              0.0893   

     second_outcome_prob  kl_divergence  off_by_perc  
120               0.0966       0.101590         9.66  
148               0.0950       0.099820         9.50  
194               0.9107       0.093542         8.93

In [5]:
div_data.loc[div_data["kl_divergence"]>=2.0]

currentAnswer                                          id  \
52             no  0x927beda324bfd4514a7b64ab5594451fdaf4796e   
293           yes  0x90bb15982f2b5a5f044ad8ff49fe20daddfb8ca7   
315            no  0x29462bf8c8f24772cd6da03878a4aee5c5813474   
323           yes  0x0ad9d4edb0a401ec9a5b4f2ccf7942d28c29d4e3   

    openingTimestamp market_creator    opening_datetime  first_outcome_prob  \
52        1722816000     quickstart 2024-08-05 02:00:00              0.8792   
293       1724803200     quickstart 2024-08-28 02:00:00              0.1166   
315       1724976000          pearl 2024-08-30 02:00:00              0.9416   
323       1724976000     quickstart 2024-08-30 02:00:00              0.0499   

     second_outcome_prob  kl_divergence  off_by_perc  
52                0.1208       2.113619        87.92  
293               0.8834       2.149006        88.34  
315               0.0584       2.840439        94.16  
323               0.9501       2.997734        95.01

In [7]:
div_data.kl_divergence.values

array([0.20518085, 0.22002342, 1.19369249, 0.64569124, 0.42663767,
       0.57075257, 1.01638735, 0.5982007 , 0.64454751, 0.26958024,
       0.83517168, 0.29249363, 1.09481949, 0.22991644, 0.45381537,
       0.83263916, 0.87299181, 0.77522529, 0.12908415, 0.84653149,
       0.23736926, 0.66281198, 0.5982007 , 1.76960666, 0.52087596,
       0.40481532, 0.82485167, 0.1710256 , 0.31937916, 0.35796149,
       0.28621648, 0.16960278, 0.65488847, 0.34150488, 0.57057563,
       1.38509508, 0.34220866, 1.03310549, 0.68438567, 1.48943512,
       0.61971086, 1.15708922, 0.58429278, 0.14560397, 1.24931891,
       1.24514208, 1.10352433, 0.25000101, 0.93547355, 0.42801751,
       0.13570518, 0.64454751, 2.11361899, 1.06740436, 0.49823851,
       0.51835389, 0.3749844 , 0.23521613, 0.49495227, 0.32739357,
       1.11596193, 0.23041996, 1.30453006, 0.36744704, 0.84257569,
       0.36614825, 0.66281198, 1.20130969, 0.37483891, 1.72484876,
       1.16539332, 0.21245092, 0.8672625 , 0.20998056, 0.57412

In [ ]:
all_markets = closed_markets.copy(deep=True)
    all_markets["market_creator"] = "all"

    # merging both dataframes
    final_markets = pd.concat([div_data, all_markets], ignore_index=True)
    final_markets = final_markets.sort_values(by="opening_datetime", ascending=True)

    # Create the main figure and axis
    fig, ax1 = plt.subplots(figsize=(10, 6))

    # Create the boxplot using seaborn
    sns.boxplot(
        data=closed_markets,
        x="month_year_week",
        y="kl_divergence",
        ax=ax1,
        hue="market_creator",
        order=["pearl", "quickstart", "all"],
    )

    # Set labels and title for the main axis
    ax1.set_xlabel("Week")
    ax1.set_ylabel("KL Divergence")
    ax1.set_title("KL Divergence Boxplot with Off-by Percentage")

    # Create a secondary y-axis
    ax2 = ax1.twinx()

    # Plot the off_by_perc values on the secondary y-axis
    for i, week in enumerate(closed_markets["month_year_week"].unique()):
        off_by_perc = closed_markets[closed_markets["month_year_week"] == week][
            "off_by_perc"
        ]
        ax2.scatter([i] * len(off_by_perc), off_by_perc, color="red", alpha=0.01)

    # Set label for the secondary y-axis
    ax2.set_ylabel("Off-by Percentage")

    # Adjust the layout and display the plot
    plt.tight_layout()